## Run this notebook

You can launch this notebook in VEDA JupyterHub by clicking the link below.

[Launch in VEDA JupyterHub (requires access)](https://nasa-veda.2i2c.cloud/hub/user-redirect/git-pull?repo=https://github.com/NASA-IMPACT/veda-docs&urlpath=lab/tree/veda-docs/contributing/dataset-ingestion/notebooks/new-item.ipynb&branch=main) 

<details><summary>Learn more</summary>
    
### Inside the Hub

This notebook was written on a VEDA JupyterHub instance

See (VEDA Analytics JupyterHub Access)[https://nasa-impact.github.io/veda-docs/veda-jh-access.html] for information about how to gain access.

### Outside the Hub

You are welcome to run this anywhere you like (Note: alternatively you can run this on https://daskhub.veda.smce.nasa.gov/, MAAP, locally, ...), just make sure that the data is accessible, or get in contact with the VEDA team to enable access.

</details>

## Install extra packages

In [1]:
!pip install -U rio_stac parse xpystac pystac nbss-upload --quiet

In [2]:
from parse import parse
from datetime import datetime
import rio_stac
import xarray as xr
import hvplot.xarray

## Create `pystac.Item`

In this section we will be creating a `pystac.Item` object. This is the part of that notebook that you should update.

### Declare constants

Start by declaring some string fields.

In [3]:
COLLECTION_ID = "no2-monthly-diff"
ITEM_ID = "OMI_trno2_0.10x0.10_202212_Col3_V4.nc"
SOURCE = "s3://veda-data-store-staging/no2-monthly-diff/OMI_trno2_0.10x0.10_202212_Col3_V4.nc.tif"

### Calculate datetime

Create a function that calculates datetime when given an `item_id`. You can change this to depend on the `source` instead if that works better.

In [4]:
def datetime_func(item_id: str) -> datetime:
    """Given the item_id, figure out the datetime"""
    
    fields = parse("OMI_trno2_0.10x0.10_{year:4}{month:2}_Col3_V4.nc", item_id)
    year = int(fields["year"])
    month = int(fields["month"])
    day = 1
    return datetime(year, month, day)

Test out the datetime function:

In [5]:
datetime_func(ITEM_ID)

datetime.datetime(2022, 12, 1, 0, 0)

### Put it together

Now take your constants and datetime function and create the STAC Item using `rio_stac`.

In [6]:
item = rio_stac.stac.create_stac_item(
  id=ITEM_ID,
  source=SOURCE,
  collection=COLLECTION_ID, 
  input_datetime=datetime_func(ITEM_ID),
  with_proj=True,
  with_raster=True,
  asset_name="cog_default",
  asset_roles=["data", "layer"],
  asset_media_type="image/tiff; application=geotiff; profile=cloud-optimized",
)

## Try it out!

Now that you have an item you can try it out and make sure it looks good and passes validation checks.

In [7]:
item.validate()

['https://schemas.stacspec.org/v1.0.0/item-spec/json-schema/item.json',
 'https://stac-extensions.github.io/projection/v1.1.0/schema.json',
 'https://stac-extensions.github.io/raster/v1.1.0/schema.json']

In [8]:
item.to_dict()

{'type': 'Feature',
 'stac_version': '1.0.0',
 'id': 'OMI_trno2_0.10x0.10_202212_Col3_V4.nc',
 'properties': {'proj:epsg': 4326,
  'proj:geometry': {'type': 'Polygon',
   'coordinates': [[[-180.0, -90.0],
     [180.0, -90.0],
     [180.0, 90.0],
     [-180.0, 90.0],
     [-180.0, -90.0]]]},
  'proj:bbox': [-180.0, -90.0, 180.0, 90.0],
  'proj:shape': [1800, 3600],
  'proj:transform': [0.1, 0.0, -180.0, 0.0, -0.1, 90.0, 0.0, 0.0, 1.0],
  'proj:projjson': {'$schema': 'https://proj.org/schemas/v0.5/projjson.schema.json',
   'type': 'GeographicCRS',
   'name': 'WGS 84',
   'datum': {'type': 'GeodeticReferenceFrame',
    'name': 'World Geodetic System 1984',
    'ellipsoid': {'name': 'WGS 84',
     'semi_major_axis': 6378137,
     'inverse_flattening': 298.257223563}},
   'coordinate_system': {'subtype': 'ellipsoidal',
    'axis': [{'name': 'Geodetic latitude',
      'abbreviation': 'Lat',
      'direction': 'north',
      'unit': 'degree'},
     {'name': 'Geodetic longitude',
      'abbrev

### Plot it (optional)

Create a quick visual to make sure that data loads and visualizes properly.

In [9]:
data = xr.open_dataset(item).cog_default.isel(time=0)
data

<xarray.DataArray 'cog_default' (y: 1800, x: 3600)>
[6480000 values with dtype=float64]
Coordinates:
    time            datetime64[ns] 2022-12-01
    id              <U37 ...
  * x               (x) float64 -180.0 -179.9 -179.8 ... 179.7 179.8 179.9
  * y               (y) float64 90.0 89.9 89.8 89.7 ... -89.6 -89.7 -89.8 -89.9
    proj:transform  object ...
    proj:projjson   object ...
    proj:epsg       int64 ...
    proj:bbox       object ...
    proj:shape      object ...
    proj:geometry   object ...
    raster:bands    object ...
    epsg            int64 ...

In [10]:
color_range = tuple(data.quantile([.02, .98]).values)

In [11]:
data.hvplot("x", "y", clim=color_range, cmap="jet", rasterize=True)

:DynamicMap   []
   :Image   [x,y]   (cog_default)

NOTE: Jet is a bad colormap because it overemphasizes certain values, but it has a very large number of colors so it is good for spotting odd patterns in the data.

## Upload this notebook

You can upload the notebook to anyplace you like, but one of the easiest ones is [notebook sharing space](https://notebooksharing.space/). Just change the following cell from "Raw" to "Code", run it and copy the output link.

<div class="alert-warning">
    
Before uploading make sure:
1) you have not hard-coded any secrets or access keys.
2) you have saved this notebook. Hint (ctrl+s) will do it
    
</div>